In [1]:
# Benders decomposition for Fixed Charge Transportation Problem

import gurobipy as gp
from gurobipy import *
import numpy as np

In [2]:
#part a)
# solve with example in lecture
capacity = [5,8,7]
demand = [3,6,6,5]

locations = len(capacity)
customers = len(demand)

varcost = [[4,5,2,7],[5,8,6,2],[8,9,4,3]]
fixcost = [[2,10,1,5],[7,2,7,8],[4,0,3,9]]

bigM = 10
#bigM = [[1000 for j in range(customers)] for i in range(locations)]

In [3]:
# Define Benders subproblem
        
def subproblem(model, where):
    if where == GRB.Callback.MIPSOL:
        v_y = model.cbGetSolution(model._y)
        #print('\nCurrent y: ', v_y)
        
        LB = model.cbGetSolution(model._z)
        print('Current LB: ', LB, '\n')
        print(model.cbGet(GRB.Callback.MIPSOL_OBJBND))
        print(model.cbGet(GRB.Callback.MIPSOL_OBJBST))
        
        bsp = gp.Model("Subproblem") 
        #variables
        x = {}
        for i in range(locations):
            for j in range(customers):
                x[i,j] = bsp.addVar(obj=varcost[i][j])
        
        #unserved demand
        s = {}
        add_cost = np.max(fixcost)*2
        for j in range(customers):
            s[j] = bsp.addVar(obj = add_cost)
        
        #demand constraint
        demand_constr = {} 
        for j in range(customers):
            demand_constr[j] = bsp.addConstr(sum(x[i,j] for i in range(locations)) + s[j] >= demand[j])
        
        #capacity constraint
        cap_constr = {}
        for i in range(locations):
            cap_constr[i] = bsp.addConstr(sum(x[i,j] for j in range(customers)) <= capacity[i])
        
        #logical constraint
        log_constr = {}
        for i in range(locations):
            for j in range(customers):
                log_constr[i,j] = bsp.addConstr(x[i,j] <= v_y[i,j] * bigM)
        
        bsp.optimize()
        
        
        #update ub and lb
        fc = 0
        for i in range(locations):
            for j in range(customers):
                if x[i,j].x > 0: 
                    fc+=fixcost[i][j]
                
        if bsp.objVal + fc > LB:
            v = np.zeros(customers) #dual of demand constraints
            for j in range(customers):
                v[j] = demand_constr[j].pi #get dual value
            
            w = np.zeros((locations,customers)) #dual of logical constraints
            for i in range(locations):
                for j in range(customers):
                    w[i,j] = log_constr[i,j].pi
            
            u = np.zeros(locations) #dual of capacity constraints
            for i in range(locations):
                u[i] = cap_constr[i].pi
            
                       
            model.cbLazy(model._z >= sum(demand[j] * v[j] for j in range(customers)) +   
                         sum(capacity[i] * u[i] for i in range(locations)) + 
                         sum(bigM * w[i][j] * model._y[i,j] for i in range(locations) for j in range(customers)) + 
                        sum(fixcost[i][j] * model._y[i,j] for i in range(locations) for j in range(customers)))

        
#        if bsp.objVal + fc < model.cbGet(GRB.Callback.MIPSOL_OBJBST):
#            model.cbLazy(model._z <= bsp.objVal + fc)
        
        
        # save result of x from subproblem
        global transport
        for i in range(locations):
            for j in range(customers):
                transport[i,j] = x[i,j].x
        #print(transport)
        print([s[j].x for j in range(customers)])
        #print(bsp.objVal)

        bsp.dispose()
                      

In [4]:
def masterproblem(MIPGap = None, TimeLimit = None):
    global m
    
    # Relaxed Master problem function
    y = {}
    z = m.addVar(obj=1)                                                                           
    for i in range(locations):
        for j in range(customers):
            y[i,j] = m.addVar(vtype=GRB.BINARY)
            
    for j in range(customers):
        m.addConstr(sum(y[i,j] for i in range(locations)) >= 1 )
        
    for i in range(locations):
        m.addConstr(sum(y[i,j] for j in range(customers)) >= 1 )

    m.Params.lazyConstraints = 1
    m._y = y
    m._z = z
    
    if MIPGap is not None: m.Params.MIPGap = MIPGap
    if TimeLimit is not None: m.Params.TimeLimit = TimeLimit
    m.optimize(subproblem)


    print("Objective: " + str(m.objVal))

    print("Solution:")
    import pandas as pd
    index = ['Source ' + str(x) for x in range(locations)]
    columns = ['Customer ' + str(x) for x in range(customers)]

    solution = pd.DataFrame(index=index, columns=columns)

    for i in range(locations):
        for j in range(customers):
            solution.iloc[i,j] = transport[i,j]

    print(solution)
    print([y[i,j].x for i in range(locations) for j in range(customers)])
    #m.dispose()

In [5]:
# solve problem with Benders decomposition
transport = np.zeros((locations, customers)) # to save result of x from subproblem
m = gp.Model("Benders Fixed Charge Transportation Masterproblem") # to save model
masterproblem()

Using license file C:\Users\hadao\gurobi.lic
Academic license - for non-commercial use only
Changed value of parameter lazyConstraints to 1
   Prev: 0  Min: 0  Max: 1  Default: 0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 7 rows, 13 columns and 24 nonzeros
Model fingerprint: 0x4e10bafe
Variable types: 1 continuous, 12 integer (12 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Current LB:  0.0 

-1e+100
0.0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 19 rows, 16 columns and 40 nonzeros
Model fingerprint: 0xca28d864
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+00, 2e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+00, 1e+01]
Presolve removed 12 rows and 0 columns
Presolve time: 0.00s
Presolved: 7 rows, 16 columns, 28 nonzeros

Iteration    Objective      


Solved in 5 iterations and 0.01 seconds
Optimal objective  1.550000000e+02
[0.0, 5.0, 0.0, 0.0]
Current LB:  109.99999999999996 

0.0
109.99999999999996
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 19 rows, 16 columns and 40 nonzeros
Model fingerprint: 0x21694811
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+00, 2e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+00, 1e+01]
Presolve removed 14 rows and 8 columns
Presolve time: 0.00s
Presolved: 5 rows, 8 columns, 10 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   1.000000e+01   0.000000e+00      0s
       5    1.5400000e+02   0.000000e+00   0.000000e+00      0s

Solved in 5 iterations and 0.00 seconds
Optimal objective  1.540000000e+02
[0.0, 0.0, 3.0, 0.0]
Current LB:  110.99999999999999 

0.0
110.99999999999999
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 19 rows, 16 colum

Presolve time: 0.00s
Presolved: 6 rows, 10 columns, 15 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    0.0000000e+00   1.000000e+01   0.000000e+00      0s
       5    9.9000000e+01   0.000000e+00   0.000000e+00      0s

Solved in 5 iterations and 0.01 seconds
Optimal objective  9.900000000e+01
[0.0, 0.0, 0.0, 0.0]
     0     0  101.34839    0    5  114.00000  101.34839  11.1%     -    0s
Current LB:  112.99999999999999 

101.3483870967742
112.99999999999999
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 19 rows, 16 columns and 40 nonzeros
Model fingerprint: 0x945bc944
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [2e+00, 2e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e+00, 1e+01]
Presolve removed 15 rows and 9 columns
Presolve time: 0.00s
Presolved: 4 rows, 7 columns, 10 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.0000000e+01   7.

In [6]:
#part b)
# solve with large example in database

In [7]:
file = open('36.txt','r')
data = file.readlines()

[locations, customers] = [int(x) for x in data[0].split(' ')]
capacity = [int(data[1].split(' ')[i]) for i in range(locations) ]
demand = [int(data[2].split(' ')[j]) for j in range(customers) ]
fixcost = [ [ int(data[i+3].split('   ')[j]) for j in range(customers) ] for i in range(locations)]
varcost = [ [ int(x) for x in data[i+3+locations+1].split('    ') if x!=''] for i in range(locations)]

print(locations)
print(customers)
print(capacity)
print(demand)
varcost

15
15
[20, 18, 17, 15, 15, 10, 10, 10, 9, 8, 6, 5, 5, 4, 4]
[20, 17, 16, 15, 13, 12, 11, 10, 10, 9, 7, 7, 7, 1, 1]


[[27, 35, 19, 32, 16, 19, 21, 21, 10, 12, 32, 14, 31, 10, 14],
 [20, 23, 20, 25, 24, 13, 21, 17, 23, 37, 16, 7, 12, 26, 35],
 [34, 22, 20, 12, 24, 29, 31, 9, 36, 27, 15, 38, 14, 33, 27],
 [17, 38, 23, 9, 34, 20, 29, 16, 26, 27, 24, 12, 27, 18, 27],
 [14, 35, 14, 27, 14, 24, 33, 31, 12, 34, 19, 31, 36, 33, 31],
 [27, 27, 23, 30, 30, 26, 22, 36, 34, 29, 31, 23, 27, 32, 25],
 [21, 30, 19, 14, 13, 24, 8, 15, 21, 31, 19, 26, 9, 13, 11],
 [9, 32, 24, 33, 23, 33, 24, 15, 30, 26, 9, 28, 37, 20, 18],
 [14, 31, 34, 23, 22, 9, 20, 37, 13, 9, 12, 38, 7, 27, 28],
 [30, 20, 23, 11, 35, 32, 32, 13, 34, 29, 27, 18, 30, 35, 30],
 [19, 32, 11, 17, 28, 28, 18, 9, 37, 9, 28, 14, 9, 13, 36],
 [29, 25, 30, 32, 24, 10, 28, 29, 18, 12, 13, 10, 29, 26, 8],
 [28, 12, 34, 25, 34, 33, 21, 19, 20, 21, 25, 26, 34, 21, 35],
 [28, 28, 11, 21, 9, 33, 9, 21, 13, 10, 23, 27, 22, 10, 36],
 [18, 19, 27, 32, 36, 30, 14, 21, 16, 15, 21, 34, 17, 31, 30]]

In [8]:
bigM = 50

In [ ]:
# solve problem with Benders decomposition
transport = np.zeros((locations, customers)) # to save result of x from subproblem
m = gp.Model("Benders Fixed Charge Transportation Masterproblem") # to save model
masterproblem(TimeLimit = 5400)

Changed value of parameter lazyConstraints to 1
   Prev: 0  Min: 0  Max: 1  Default: 0
Changed value of parameter TimeLimit to 5400.0
   Prev: inf  Min: 0.0  Max: inf  Default: inf
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 30 rows, 226 columns and 450 nonzeros
Model fingerprint: 0x1e6e75a5
Variable types: 1 continuous, 225 integer (225 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [1e+00, 1e+00]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+00]
Current LB:  0.0 

-1e+100
0.0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0xc5fe7553
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 225 rows and 0 columns
Presolve time: 0.01s
Presolved: 30 rows, 240 columns, 465 nonzeros

Iteration    O

Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x5831379d
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 240 rows and 211 columns
Presolve time: 0.00s
Presolved: 15 rows, 29 columns, 37 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    4.8701000e+04   5.400000e+01   0.000000e+00      0s
      15    8.3936000e+04   0.000000e+00   0.000000e+00      0s

Solved in 15 iterations and 0.01 seconds
Optimal objective  8.393600000e+04
[0.0, 8.0, 11.0, 5.0, 0.0, 6.0, 1.0, 10.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Current LB:  93381.99999999997 

0.0
93381.99999999997
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x5831379d
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
 

  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 238 rows and 209 columns
Presolve time: 0.00s
Presolved: 17 rows, 31 columns, 43 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    2.8631000e+04   5.650000e+01   0.000000e+00      0s
      17    3.8669000e+04   0.000000e+00   0.000000e+00      0s

Solved in 17 iterations and 0.01 seconds
Optimal objective  3.866900000e+04
[0.0, 8.0, 0.0, 5.0, 0.0, 0.0, 1.0, 4.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
     0     0    0.00000    0    7 93382.0000    0.00000   100%     -    0s
     0     0    0.00000    0    7 93382.0000    0.00000   100%     -    0s
Current LB:  0.0 

0.0
0.0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0xc92f086e
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+

Presolve time: 0.02s
Presolved: 14 rows, 28 columns, 37 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.4586000e+04   4.700000e+01   0.000000e+00      0s
      15    9.3857000e+04   0.000000e+00   0.000000e+00      0s

Solved in 15 iterations and 0.03 seconds
Optimal objective  9.385700000e+04
[10.0, 3.0, 11.0, 5.0, 0.0, 5.0, 1.0, 10.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0]
Current LB:  79609.00000000001 

0.0
79609.00000000001
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x37ca8853
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 239 rows and 209 columns
Presolve time: 0.00s
Presolved: 16 rows, 31 columns, 42 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.2438000e+04   5.500000e+01   0.000000e+

Presolve removed 246 rows and 224 columns
Presolve time: 0.00s
Presolved: 9 rows, 16 columns, 20 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    8.7117000e+04   2.650000e+01   0.000000e+00      0s
       9    1.0611100e+05   0.000000e+00   0.000000e+00      0s

Solved in 9 iterations and 0.01 seconds
Optimal objective  1.061110000e+05
[5.0, 12.0, 11.0, 9.0, 0.0, 3.0, 1.0, 6.0, 2.0, 0.0, 0.0, 3.0, 0.0, 0.0, 0.0]
Current LB:  88311.00000000132 

6009.275993960745
88311.00000000132
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x9e596661
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e-14, 5e+01]
Presolve removed 231 rows and 192 columns
Presolve time: 0.00s
Presolved: 24 rows, 48 columns, 75 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time


...

[0.0, 0.0, 5.0, 11.0, 3.0, 3.0, 1.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Current LB:  8829.0 

6494.811336303265
8829.0
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x5d1dd7ee
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [3e-15, 5e+01]
Presolve removed 240 rows and 213 columns
Presolve time: 0.01s
Presolved: 15 rows, 27 columns, 37 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.2954000e+04   4.900000e+01   0.000000e+00      0s
Extra 20 simplex iterations after uncrush
      34    4.2719000e+04   0.000000e+00   0.000000e+00      0s

Solved in 34 iterations and 0.01 seconds
Optimal objective  4.271900000e+04
[0.0, 0.0, 0.0, 11.0, 3.0, 3.0, 1.0, 0.0, 2.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Current LB:  8661.999999999998 

6494.847328063063
8661.999999999998
Gurob

Extra 4 simplex iterations after uncrush
      20    8.2582000e+04   0.000000e+00   0.000000e+00      0s

Solved in 20 iterations and 0.02 seconds
Optimal objective  8.258200000e+04
[12.0, 2.0, 12.0, 5.0, 8.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0]
Current LB:  8973.999999999998 

6495.157541781902
8973.999999999998
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0x33cc60d5
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 240 rows and 213 columns
Presolve time: 0.01s
Presolved: 15 rows, 27 columns, 34 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.8990000e+04   5.400000e+01   0.000000e+00      0s
      15    8.0706000e+04   0.000000e+00   0.000000e+00      0s

Solved in 15 iterations and 0.02 seconds
Optimal objective  8.07

Presolve time: 0.01s
Presolved: 11 rows, 19 columns, 24 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    2.9024000e+04   4.000000e+01   0.000000e+00      0s
      10    3.2710000e+04   0.000000e+00   0.000000e+00      0s

Solved in 10 iterations and 0.02 seconds
Optimal objective  3.271000000e+04
[5.0, 0.0, 1.0, 0.0, 0.0, 3.0, 1.0, 0.0, 2.0, 0.0, 2.0, 0.0, 0.0, 1.0, 0.0]
Current LB:  7599.999999999998 

6495.7039824882495
7599.999999999998
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0xb8f610fa
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 241 rows and 217 columns
Presolve time: 0.01s
Presolved: 14 rows, 23 columns, 29 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    2.0760000e+04   5.450000e+01 

  RHS range        [1e+00, 5e+01]
Presolve removed 243 rows and 219 columns
Presolve time: 0.01s
Presolved: 12 rows, 21 columns, 25 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    5.0975000e+04   4.150000e+01   0.000000e+00      0s
Extra 8 simplex iterations after uncrush
      20    9.4425000e+04   0.000000e+00   0.000000e+00      0s

Solved in 20 iterations and 0.02 seconds
Optimal objective  9.442500000e+04
[0.0, 12.0, 5.0, 11.0, 0.0, 3.0, 0.0, 6.0, 9.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0]
Current LB:  9139.999999999998 

6496.081659804664
9139.999999999998
Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 240 columns and 690 nonzeros
Model fingerprint: 0xa9508821
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 5e+01]
Presolve removed 239 rows and 213 columns
Presolve time: 0.01s
Presolved: 16 rows, 27 columns, 

  Objective range  [7e+00, 2e+03]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e-15, 5e+01]
Presolve removed 245 rows and 223 columns
Presolve time: 0.01s
Presolved: 10 rows, 17 columns, 21 nonzeros

Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.5588000e+04   3.400000e+01   0.000000e+00      0s
Extra 5 simplex iterations after uncrush
      16    7.2715000e+04   0.000000e+00   0.000000e+00      0s

Solved in 16 iterations and 0.02 seconds
Optimal objective  7.271500000e+04


In [10]:
k = 1
mvars = m.getVars()
y0 = np.zeros((locations, customers))
for i in range(locations):
    for j in range(customers):
        y0[i,j] = mvars[k].x
        k+=1

In [11]:
model0 = gp.Model()
x0 = {}
for i in range(locations):
    for j in range(customers):
        x0[i,j] = model0.addVar(obj=varcost[i][j])

#demand constraint
demand_constr = {} 
for j in range(customers):
    demand_constr[j] = model0.addConstr(sum(x0[i,j] for i in range(locations)) == demand[j])
        
#capacity constraint
cap_constr = {}
for i in range(locations):
    cap_constr[i] = model0.addConstr(sum(x0[i,j] for j in range(customers)) <= capacity[i])

#logical constraint
log_constr = {}
for i in range(locations):
    for j in range(customers):
        log_constr[i,j] = model0.addConstr(x0[i,j] <= y0[i,j] * min(capacity[i], demand[j]))

model0.optimize()

print("Objective: " + str(model0.objVal))

print("Solution:")
import pandas as pd
index = ['Source ' + str(x) for x in range(locations)]
columns = ['Customer ' + str(x) for x in range(customers)]

solution = pd.DataFrame(index=index, columns=columns)

for i in range(locations):
    for j in range(customers):
        solution.iloc[i,j] = x0[i,j].x

print(solution)

Gurobi Optimizer version 9.0.2 build v9.0.2rc0 (win64)
Optimize a model with 255 rows, 225 columns and 675 nonzeros
Model fingerprint: 0xcaf3d292
Coefficient statistics:
  Matrix range     [1e+00, 1e+00]
  Objective range  [7e+00, 4e+01]
  Bounds range     [0e+00, 0e+00]
  RHS range        [1e+00, 2e+01]
Presolve removed 255 rows and 225 columns
Presolve time: 0.01s
Presolve: All rows and columns removed
Iteration    Objective       Primal Inf.    Dual Inf.      Time
       0    3.2210000e+03   0.000000e+00   0.000000e+00      0s

Solved in 0 iterations and 0.01 seconds
Optimal objective  3.221000000e+03
Objective: 3221.0
Solution:
          Customer 0 Customer 1 Customer 2 Customer 3 Customer 4 Customer 5  \
Source 0           0          0          0          0         13          6   
Source 1           0          0          0          0          0          0   
Source 2           0         17          0          0          0          0   
Source 3          15          0          0  

In [12]:
model0.objVal+sum([fixcost[i][j] for i in range(locations) for j in range(customers) if x0[i,j].x > 0])

12245.0

In [13]:
sum(fixcost[i][j] for i in range(locations) for j in range(customers) if transport[i,j] > 0)

8838